In [3]:
import pandas as pd

In [142]:
from current import grid, determine_directions
class Locator:
    """ This object returns dataframes containing the information about other ships/shipyards on the map and also in the given ship's grid. """
    def __init__(self, board, ship):
        self.board = board
        self.ship = ship
        self.ship_position = ship.position
        # Get the grid
        self.grid = grid(ship.cell)

    def get_ship_info(self):
        """ Returns the info about ships in all of the board. """
        ships_info = {}

        for ship_id, ship in self.board.ships.items():
            base_info = {"my_ship": 0, "moves": 0, "position": (ship.position.x, ship.position.y),
                         'cargo': ship.cell.halite,
                         'dirX': (determine_directions(self.ship_position, ship.position))[0],
                         'dirY': (determine_directions(self.ship_position, ship.position))[1]}

            base_info['movesX'] = min(abs(self.ship_position.x - ship.position.x), abs(21 - self.ship_position.x + ship.position.x))
            base_info['movesY'] = min(abs(self.ship_position.y - ship.position.y), abs(21 - self.ship_position.y + ship.position.y))
            base_info['moves'] = base_info['movesX'] + base_info['movesY']

            if ship_id in self.board.current_player.ship_ids and ship.id != self.ship.id:
                base_info['my_ship'] = 1
                ships_info[ship_id] = base_info
            elif not (ship_id in self.board.current_player.ship_ids):
                ships_info[ship_id] = base_info

        return pd.DataFrame(ships_info)

    def get_shipyard_info(self):
        """ Returns the info about shipyards in all of the board. """
        shipyards_info = {}

        for shipyard_id, shipyard in self.board.shipyards.items():
            base_info = {"my_shipyard": 0,
                         "position": (shipyard.position.x, shipyard.position.y),
                         'dirX': (determine_directions(self.ship_position, shipyard.position))[0],
                         'dirY': (determine_directions(self.ship_position, shipyard.position))[1],
                         'player_halite': shipyard.player.halite}

            base_info['movesX'] = min(abs(self.ship_position.x - shipyard.position.x), abs(21 - self.ship_position.x + shipyard.position.x))
            base_info['movesY'] = min(abs(self.ship_position.y - shipyard.position.y), abs(21 - self.ship_position.y + shipyard.position.y))
            base_info['moves'] = base_info['movesX'] + base_info['movesY']

            if shipyard_id in self.board.current_player.shipyard_ids:
                base_info['my_shipyard'] = 1
                shipyards_info[shipyard_id] = base_info
            else:
                shipyards_info[shipyard_id] = base_info

        return pd.DataFrame(shipyards_info)

    def generate_grid_df(self):
        """ Generates a Dataframe describing the information of objects and cells in the grid of the ship. """
        all_dirs = {}

        total_moves = len(self.grid) / 4
        
        for direction, cell in self.grid.items():

            base_info = {
                "ship_id": None, "shipyard_id": None,
                "my_ship": 0, "my_shipyard": 0,
                "halite": 0, "moves": 0,
                "movesX": 0, "movesY": 0,
                "dirY": 'None', "dirX": 'None',
                'weightX': 0, 'weightY': 0
            }

            if "N" in  direction:
                base_info['dirY'] = 'N'
                base_info['movesY'] = direction.count("N")
            elif "S" in  direction:
                base_info['dirY'] = 'S'
                base_info['movesY'] = direction.count("S")

            if "W" in  direction:
                base_info['dirX'] = 'W'
                base_info['movesX'] = direction.count("W")
            elif "E" in  direction:
                base_info['dirX'] = 'E'
                base_info['movesX'] = direction.count("E")

            if base_info['dirY'] != 'None':
                base_info['weightY'] = (total_moves - base_info['movesY']) / (base_info['movesY'] * total_moves)
            
            if base_info['dirX'] != 'None':
                base_info['weightX'] = (total_moves - base_info['movesX']) / (base_info['movesX'] * total_moves)


            if cell.ship is not None:
                base_info["ship_id"] = cell.ship.id
                if cell.ship.id in self.ship.player.ship_ids:
                    base_info["my_ship"] = 1

            if cell.shipyard is not None:
                base_info["shipyard_id"] = cell.shipyard.id
                if cell.shipyard.id in self.ship.player.shipyard_ids:
                    base_info['my_shipyard'] = 1

            base_info['halite'] = cell.halite
            # The number of letters in the direction would indicate the number of moves needed to get there
            base_info['moves'] = len(direction)

            all_dirs[direction] = base_info

        return pd.DataFrame(all_dirs)

In [1]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *

# Create a test environment for use later
board_size = 21
environment = make("halite", configuration={"size": board_size, "startingHalite": 30000}, debug=True)
agent_count = 4
environment.reset(agent_count)
state = environment.state[0]

In [165]:
# Change the behviour of my own movement from board.current_player
board = Board(state.observation, environment.configuration)

board.current_player.ships[0].next_action = ShipAction.CONVERT
board.ships['0-2'].next_action = ShipAction.CONVERT
board.ships['0-3'].next_action = ShipAction.CONVERT
board.ships['0-4'].next_action = ShipAction.CONVERT
board = board.next()
board.current_player.shipyards[0].next_action = ShipyardAction.SPAWN
board.shipyards['1-2'].next_action = ShipyardAction.SPAWN
board.shipyards['1-3'].next_action = ShipyardAction.SPAWN
board.shipyards['1-4'].next_action = ShipyardAction.SPAWN
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.shipyards[0].next_action = ShipyardAction.SPAWN
# Opponents
board.ships['2-2'].next_action = ShipAction.NORTH
board.shipyards['1-2'].next_action = ShipyardAction.SPAWN
board.ships['2-3'].next_action = ShipAction.WEST
board.shipyards['1-3'].next_action = ShipyardAction.SPAWN
board.ships['2-4'].next_action = ShipAction.EAST
board.shipyards['1-4'].next_action = ShipyardAction.SPAWN
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.NORTH
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.shipyards[0].next_action = ShipyardAction.SPAWN
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.shipyards['1-2'].next_action = ShipyardAction.SPAWN
board.ships['2-3'].next_action = ShipAction.NORTH
board.shipyards['1-3'].next_action = ShipyardAction.SPAWN
board.ships['2-4'].next_action = ShipAction.SOUTH
board.shipyards['1-4'].next_action = ShipyardAction.SPAWN
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.NORTH
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

board.current_player.ships[0].next_action = ShipAction.CONVERT
board = board.next()

ship = board.current_player.ships[0]
loc = Locator(board, ship)

In [134]:
board.shipyards

{'1-1': <kaggle_environments.envs.halite.helpers.Shipyard at 0x7fd147ab9c10>,
 '1-2': <kaggle_environments.envs.halite.helpers.Shipyard at 0x7fd147ab9d00>,
 '1-3': <kaggle_environments.envs.halite.helpers.Shipyard at 0x7fd147ab9df0>,
 '1-4': <kaggle_environments.envs.halite.helpers.Shipyard at 0x7fd147ab9ee0>,
 '9-1': <kaggle_environments.envs.halite.helpers.Shipyard at 0x7fd14763e970>}

In [166]:
class ShipyardDecisions:
    def __init__(self, board: Board, player):
        """
            Decides the Shipyard's next action based on the given parameters
            board: The board that we will be observing
            shipyards: All the shipyards that the player has
        """
        self.board = board
        self.step = board.observation['step']
        self.Shipyards = player.shipyards
        self.shipyard_tendencies = {}

    def determine(self):
        """ Determines which shipyards should SPAWN, returns a dictionary of id: 'SPAWN' """
        self.weight_shipyard_tendencies()
        sorted_weights = {k: v for k, v in sorted(self.shipyard_tendencies.items(), key=lambda item: item[1], reverse=True)}
        print(sorted_weights)
        shipyard_ids = []

        for shipyard_id, tendency in sorted_weights.items():
            if tendency > -10:
                shipyard_ids.append(shipyard_id)

        return shipyard_ids

    def weight_shipyard_tendencies(self):
        """ Iterates through the shipyards and weights their tendencies. """
        for shipyard in self.Shipyards:
            # Given that there are no ships on the shipyard we will weight the ship's tendency
            if shipyard.cell.ship is None:
                grid = Locator(self.board, shipyard).generate_grid_df()
                weight = self.weight(grid)

                self.shipyard_tendencies[shipyard.id] = weight

    def weight(self, grid) -> float:
        """
            The weighting system is rather simple:
                - If there was an enemy ship add to the weight
                - If there was one of my own ships, then subtract from the weight
            Take the distance of the ship into acount
        """
        # Base case: if I had no ships the spawn
        if len(self.board.current_player.ships) == 0: return 100
        value = 0
        # Iteraing through the grid
        for direction in grid.columns:
            # print(pd.isna(grid[direction].ship_id))
            if not pd.isna(grid[direction].ship_id):
                if grid[direction].my_ship == 1:
                    # ship_cargo: direct, distance: indirect
                    value -= 100 / grid[direction]['moves']
                else:
                    # Ship_cargo: direct, distance: indirect
                    value += 1000 / grid[direction]['moves']
                    
            if not pd.isna(grid[direction].shipyard_id):
                if grid[direction].my_shipyard == 0:
                    value += 200 / grid[direction]['moves']

        return value

In [131]:
ShipyardDecisions(board, board.current_player).determine()

aship 4 1
-25.0
aship 5 1
-45.0
aship 2 0
500.0
aship 2 1
450.0
483.3333333333333
{'9-1': 483.3333333333333, '1-1': -45.0}


['9-1']

In [215]:
grid = loc.generate_grid_df().T

In [228]:
grid

ship_id shipyard_id my_ship my_shipyard   halite moves movesX movesY  \
N         None        None       0           0  187.466     1      0      1   
S         None        None       0           0  191.215     1      0      1   
W         None        None       0           0  382.431     1      1      0   
E         None        None       0           0  282.041     1      1      0   
NW        None        None       0           0  152.971     2      1      1   
...        ...         ...     ...         ...      ...   ...    ...    ...   
WWWSSS    None        None       0           0        0     6      3      3   
NNNNEE    None        None       0           0    3.585     6      2      4   
NNNNWW    None        None       0           0        0     6      2      4   
SSSSWW    None        None       0           0        0     6      2      4   
SSSSEE    None        None       0           0    3.515     6      2      4   

        dirY  dirX   weightX   weightY  
N          N  None         0  0.952381  
S          S  None         0  0.952381  
W       None     W  0.952381         0  
E       None     E  0.952381         0  
NW         N     W  0.952381  0.952381  
...      ...   ...       ...       ...  
WWWSSS     S     W  0.285714  0.285714  
NNNNEE     N     E  0.452381  0.202381  
NNNNWW     N     W  0.452381  0.202381  
SSSSWW     S     W  0.452381  0.202381  
SSSSEE     S     E  0.452381  0.202381  

[84 rows x 12 columns]

In [227]:
grid.loc[pd.isna(grid['shipyard_id']) == False]

ship_id shipyard_id my_ship my_shipyard halite moves movesX movesY dirY  \
SSSSS    None         1-3       0           0      0     5      0      5    S   
NNNNN    None         1-1       0           1      0     5      0      5    N   

       dirX weightX   weightY  
SSSSS  None       0  0.152381  
NNNNN  None       0  0.152381

In [210]:
grid.iloc[1,:] == '1-1'

N         False
S         False
W         False
E         False
NW        False
          ...  
WWWSSS    False
NNNNEE    False
NNNNWW    False
SSSSWW    False
SSSSEE    False
Name: shipyard_id, Length: 84, dtype: bool

In [177]:
board.next()

In [225]:
loc.get_shipyard_info()

1-1       1-2     1-3      1-4       9-1
my_shipyard          1         0       0        0         1
position       (5, 15)  (15, 15)  (5, 5)  (15, 5)  (10, 16)
dirX              None         E    None        E         E
dirY                 N         N       S        S         N
player_halite     2500      3000    3000     3000      2500
movesX               0        10       0       10         5
movesY               5         5       5        5         6
moves                5        15       5       15        11

In [111]:
%%writefile current.py

Overwriting current.py


In [232]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *

env = make("halite", debug=True)
env.run(["random", "current.py", 'random', 'agent_a.py'])
env.render(mode="ipython", width=800, height=600)